In [1]:
# noexport

!typech train_utils_extended.ipynb

[NbConvertApp] Converting notebook train_utils_extended.ipynb to python


In [1]:
from train_utils import *

In [2]:
def train_one_epoch(model, criterion, learning_rate, train_data):
  total_loss = 0
  confusion = [[0,0,0,0],[0,0,0,0],[0,0,0,0],[0,0,0,0]]
  correct = 0
  total = 0
  for idx,item in enumerate(train_data):
    category_tensor = item['category']
    line_tensor = item['feature']
    category = tensor_to_difficulty(item['category'])
    category_i = get_difficulty_idx(category)
    if line_tensor.size()[0] == 0:
      continue
    output,loss = train_transformer(model, criterion, category_tensor, line_tensor.permute(1,0,2), learning_rate)
    total_loss += loss
    guess = prediction_to_difficulty(output)
    guess_i = get_difficulty_idx(guess)
    if guess_i == category_i:
      correct += 1
    confusion[category_i][guess_i] += 1
    total += 1
  return {
    'train_loss': total_loss,
    'train_correct': correct,
    'train_total': total,
    'train_confusion': confusion,
  }

def train_model_for_parameters(parameter_info_list, num_epochs=3):
  base_path_full = get_path_for_parameters(parameter_info_list)
  base_path = 'tm_' + convert_string_to_hash(base_path_full)
  if path.exists(base_path):
    # todo check status file and resume training
    return
  else:
    os.mkdir(base_path)
  json.dump({'base_path': base_path}, open('current.json', 'w'))
  status_info = {
    'status': 'training',
    'epoch': 0,
    'base_path': base_path,
    'base_path_full': base_path_full,
    'dataset_name': dataset_name,
    'start_time': str(arrow.get()),
    'start_timestamp': arrow.get().timestamp,
  }
  print(base_path)
  json.dump(parameter_info_list, open(path.join(base_path, 'parameters.json'), 'w'))
  model = get_model_for_parameters(parameter_info_list)
  learning_rate = get_parameter_value_for_info_list(parameter_info_list, 'learning_rate')
  train_data,dev_data,test_data = get_data_for_parameters(parameter_info_list)
  criterion = nn.NLLLoss()
  for epoch in range(1, 1 + num_epochs):
    status_info['epoch'] = epoch
    json.dump(status_info, open(path.join(base_path, 'status.json'), 'w'))
    print(status_info)
    epoch_start_time = str(arrow.get())
    epoch_start_timestamp = arrow.get().timestamp
    model_path = path.join(base_path, 'model_' + str(epoch) + '.pt')
    if path.exists(model_path):
      continue
    train_info = train_one_epoch(model, criterion, learning_rate, train_data)
    save_model(model, criterion, epoch, train_info['train_loss'], model_path)
    dev_info = evaluate_model_on_dataset(model, dev_data, 'dev_')
    test_info = evaluate_model_on_dataset(model, test_data, 'test_')
    for k,v in dev_info.items():
      train_info[k] = v
    for k,v in test_info.items():
      train_info[k] = v
    train_info['epoch_start_time'] = epoch_start_time
    train_info['epoch_start_timestamp'] = epoch_start_timestamp
    train_info['epoch_end_time'] = str(arrow.get())
    train_info['epoch_end_timestamp'] = arrow.get().timestamp
    training_start_timestamp = arrow.get().timestamp
    info_path = path.join(base_path, 'info_' + str(epoch) + '.json')
    json.dump(train_info, open(info_path, 'w'))
  status_info['status'] = 'done'
  status_info['end_time'] = str(arrow.get())
  status_info['end_timestamp'] = arrow.get().timestamp
  json.dump(status_info, open(path.join(base_path, 'status.json'), 'w'))
  print(status_info)


In [3]:
def main():
  while True:
    #parameters = sample_random_parameters(['learning_rate', 'window_embed_size', 'num_prior_entries'])
    #parameters = sample_random_parameters(['sample_difficulty_every_n_visits'])
    parameters = sample_random_parameters(['window_embed_size', 'num_prior_entries'])
    train_model_for_parameters(parameters)
    parameters = sample_random_parameters(['sample_every_n_visits'])
    train_model_for_parameters(parameters)
    


In [ ]:
main()

tm_b521d49ba17cb4d1199e8bd7208619ce29fdfa29
{'name': 'model_name', 'type': 'model', 'values': ['selfattentionlstm'], 'value': 'selfattentionlstm'}
{'name': 'criterion', 'type': 'model', 'values': ['NLLLoss'], 'value': 'NLLLoss'}
{'name': 'learning_rate', 'type': 'model', 'values': [5e-05, 0.005, 0.05, 0.0005], 'value': 5e-05}
{'name': 'window_embed_size', 'type': 'model', 'values': [256, 64, 128, 512], 'value': 128}
{'name': 'num_features', 'type': 'model', 'values': [290], 'value': 290}
running get_data_for_parameters
{'name': 'num_prior_entries', 'type': 'dataparam', 'values': [10, 20, 30, 40], 'value': 20}
{'name': 'sample_every_n_visits', 'type': 'dataparam', 'values': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 16, 32, 64, 128, 256, 512], 'value': 1}
{'name': 'sample_difficulty_every_n_visits', 'type': 'dataparam', 'values': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 16, 32, 64, 128, 256, 512], 'value': 1}
{'name': 'disable_prior_visit_history', 'type': 'dataparam', 'values': [False, True], 'value': Fal

done with computation 2019_04_25/get_collection_items/8642884bd204eafc660a04a2_internal:choose_difficulty.msgpack
9ca53f1f33ac3e25c2e3f3d2
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/9ca53f1f33ac3e25c2e3f3d2_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/9ca53f1f33ac3e25c2e3f3d2_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/9ca53f1f33ac3e25c2e3f3d2_synced:experiment_vars.msgpack for arg 9ca53f1f33ac3e25c2e3f3d2_synced:experiment_vars
done with computation 2019_04_25/get_collection_items/9ca53f1f33ac3e25c2e3f3d2_synced:experiment_vars.msgpack
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/9ca53f1f33ac3e25c2e3f3d2_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/9ca53f1f33ac3e25c2e3f3d2_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/9ca53f1f33ac3e2

done with computation 2019_04_25/get_collection_items/f32cf25130f6fa751892960e_internal:choose_difficulty.msgpack
8f77439cf19de38abfd4a417
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/8f77439cf19de38abfd4a417_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/8f77439cf19de38abfd4a417_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/8f77439cf19de38abfd4a417_synced:experiment_vars.msgpack for arg 8f77439cf19de38abfd4a417_synced:experiment_vars
done with computation 2019_04_25/get_collection_items/8f77439cf19de38abfd4a417_synced:experiment_vars.msgpack
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/8f77439cf19de38abfd4a417_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/8f77439cf19de38abfd4a417_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/8f77439cf19de38

done with computation 2019_04_25/get_collection_items/cb266f371364b060f117b6a1_internal:choose_difficulty.msgpack
4e69f3aebac131196a8f2912
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/4e69f3aebac131196a8f2912_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/4e69f3aebac131196a8f2912_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/4e69f3aebac131196a8f2912_synced:experiment_vars.msgpack for arg 4e69f3aebac131196a8f2912_synced:experiment_vars
done with computation 2019_04_25/get_collection_items/4e69f3aebac131196a8f2912_synced:experiment_vars.msgpack
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/4e69f3aebac131196a8f2912_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/4e69f3aebac131196a8f2912_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/4e69f3aebac1311

exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/414492408538c282663be78d_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/414492408538c282663be78d_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/414492408538c282663be78d_internal:choose_difficulty.msgpack for arg 414492408538c282663be78d_internal:choose_difficulty
done with computation 2019_04_25/get_collection_items/414492408538c282663be78d_internal:choose_difficulty.msgpack
8880741c0eb16b95ba062848
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/8880741c0eb16b95ba062848_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/8880741c0eb16b95ba062848_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/8880741c0eb16b95ba062848_synced:experiment_vars.msgpack for arg 8880741c0eb16b95ba062848_synced:experiment_vars
done 

...

done with computation 2019_04_25/get_collection_items/a9a2f094d9b8ae4bc254e3f1_synced:experiment_vars.msgpack
5193c2ee0d637150db7b560f
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/5193c2ee0d637150db7b560f_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/5193c2ee0d637150db7b560f_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/5193c2ee0d637150db7b560f_synced:experiment_vars.msgpack for arg 5193c2ee0d637150db7b560f_synced:experiment_vars
done with computation 2019_04_25/get_collection_items/5193c2ee0d637150db7b560f_synced:experiment_vars.msgpack
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/5193c2ee0d637150db7b560f_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/5193c2ee0d637150db7b560f_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/5193c2ee0d637150db7

done with computation 2019_04_25/get_collection_items/78a1fbcbd679096185990a78_internal:choose_difficulty.msgpack
d19dda1cf578fcc3ee503bf0
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/d19dda1cf578fcc3ee503bf0_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/d19dda1cf578fcc3ee503bf0_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/d19dda1cf578fcc3ee503bf0_synced:experiment_vars.msgpack for arg d19dda1cf578fcc3ee503bf0_synced:experiment_vars
done with computation 2019_04_25/get_collection_items/d19dda1cf578fcc3ee503bf0_synced:experiment_vars.msgpack
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/d19dda1cf578fcc3ee503bf0_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/d19dda1cf578fcc3ee503bf0_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/d19dda1cf578fcc

exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/b13b5888c115c70bc00580c1_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/b13b5888c115c70bc00580c1_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/b13b5888c115c70bc00580c1_internal:choose_difficulty.msgpack for arg b13b5888c115c70bc00580c1_internal:choose_difficulty
done with computation 2019_04_25/get_collection_items/b13b5888c115c70bc00580c1_internal:choose_difficulty.msgpack
a148893a8c625ca26054d748
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/a148893a8c625ca26054d748_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/a148893a8c625ca26054d748_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/a148893a8c625ca26054d748_synced:experiment_vars.msgpack for arg a148893a8c625ca26054d748_synced:experiment_vars
done 

done with computation 2019_04_25/get_collection_items/6312a2a71faf099b1b8463e5_synced:experiment_vars.msgpack
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/6312a2a71faf099b1b8463e5_internal:choose_difficulty.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/6312a2a71faf099b1b8463e5_internal:choose_difficulty.msgpack'
performing computation 2019_04_25/get_collection_items/6312a2a71faf099b1b8463e5_internal:choose_difficulty.msgpack for arg 6312a2a71faf099b1b8463e5_internal:choose_difficulty
done with computation 2019_04_25/get_collection_items/6312a2a71faf099b1b8463e5_internal:choose_difficulty.msgpack
d5b91eced831728154c2330f
exception in msgpackmemo1arg for file 2019_04_25/get_collection_items/d5b91eced831728154c2330f_synced:experiment_vars.msgpack
[Errno 2] No such file or directory: '2019_04_25/get_collection_items/d5b91eced831728154c2330f_synced:experiment_vars.msgpack'
performing computation 2019_04_25/get_collection_items/d5b91ec

all_features_data is
<class 'dict'>
